<h1>Purpose Create a H2O Model and Add to MLflow<h1>

# Install and import the required libraries.

Ensure that the libraries are added to the cluster.

In [ ]:
pip install h2o

In [ ]:
pip install h2oai_mlflow_flavors

In [ ]:
import h2o
import mlflow
import h2osteam
from h2osteam.clients import H2oClient
from h2osteam.clients import H2oKubernetesClient
from h2o.estimators import H2ODeepLearningEstimator
from h2o_mlflow_flavors.h2o3 import log_model

# Login to Steam and create H2O3 clusters

In [ ]:
h2osteam.login(url="https://steam.cloud-qa.h2o.ai/", username="<username>",password="<steam_token>", verify_ssl=True)

In [ ]:
h2osteam.print_profiles()
h2osteam.print_python_environments()

In [ ]:
H2oKubernetesClient().get_clusters()

In [ ]:
cluster_name="<name_chosen_for_cluster>"
try:
  cluster = H2oKubernetesClient.get_cluster(cluster_name)
  cluster.connect()  
except:
  print("Cluster is not running")

In [ ]:
cluster = H2oKubernetesClient.launch_cluster(name=cluster_name,
                                   profile_name="default-h2o-kubernetes",
                                   version="3.38.0.3",
                                               node_count=4,
                                                cpu_count=1,
                                               gpu_count=0,
                                               memory_gb=4,
                                               max_idle_h=2,
                                               max_uptime_h=8,
                                               timeout_s=600  

## Connect to the cluster

In [ ]:
while 1:
  if cluster.is_running():
    cluster.connect() 
    break

In [ ]:
h2o.ls()

# Ensure the dataset is available in the location. Or modify the path to the location wherein the file is available.

In [ ]:
insurancePath="/dbfs/FileStore/tables/insurance.csv"
insurance = h2o.upload_file(insurancePath)

# Preprocess data

In [ ]:
insurance["offset"] = insurance["Holders"].log()
insurance["Group"] = insurance["Group"].asfactor()
insurance["Age"] = insurance["Age"].asfactor()
insurance["District"] = insurance["District"].asfactor()

# Train the model

In [ ]:
# hyperparameter 
#----------------------------------------hyperparameter---------------------------------------------#

distribution="tweedie"
hidden=[1]
epochs=1000
train_samples_per_iteration=-1
reproducible=True
activation="Tanh"
single_node_mode=False
balance_classes=False
force_load_balance=False
seed=23123
tweedie_power=1.5
score_training_samples=0
score_validation_samples=0
stopping_rounds=0
#---------------------------------------- Build and train the model-------------------------------------------------------#
# Build and train the model:
dl = H2ODeepLearningEstimator(distribution=distribution,
                           hidden=hidden,
                           epochs=epochs,
                           train_samples_per_iteration=train_samples_per_iteration,
                           reproducible=reproducible,
                           activation=activation,
                           single_node_mode=single_node_mode,
                           balance_classes=balance_classes,
                           force_load_balance=force_load_balance,
                           seed=seed,
                           tweedie_power=tweedie_power,
                           score_training_samples=score_training_samples,
                           score_validation_samples=score_validation_samples,
                           stopping_rounds=stopping_rounds)
#_-----------------Training------------------------------------------#
dl.train(x=list(range(3)),
    y="Claims",
    training_frame=insurance)

# Download the model as a MOJO

In [ ]:
artifact_location = dl.download_mojo('/dbfs/FileStore/H2O3/')
print(artifact_location)

# Add the model to MLflow

## Add signatures

In [ ]:
target='Claims'
schema = []
for column in insurance.columns:
    colspec = mlflow.types.ColSpec(name=column, type=mlflow.types.DataType.long)
    schema.append(colspec)
    
input_schema = mlflow.types.Schema(inputs=schema)

output_schema = mlflow.types.Schema(
    inputs=[
        mlflow.types.ColSpec(name=target, type=mlflow.types.DataType.long)
    ]
)

model_signature = mlflow.models.ModelSignature(
    inputs=input_schema, outputs=output_schema
)

## Register the model.

In [ ]:
log_model(h2o3_artifact_location=artifact_location, artifact_path ="h2o3_mojo", registered_model_name="<Name for the registered model>")
mlflow.end_run()